In [3]:
!pip install transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.9/7.9 MB 46.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.0/302.0 kB 29.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 99.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 61.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 27.5 MB/s eta 0:00:00


In [4]:
!huggingface-cli login
#from huggingface_hub import notebook_login
#notebook_login()


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|
    
    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Token: 
Add token as git credential? (Y/n) y
Token is valid (permission: write).
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub.
Run the following command in your terminal in case you want to set the 'store' cr

In [11]:
from huggingface_hub import from_pretrained_keras

model = from_pretrained_keras("mabzak/lstm-id-yt-comment")

config.json not found in HuggingFace Hub.


Fetching 8 files:   0%|          | 0/8 [00:00<?, ?it/s]

In [13]:
from tensorflow.keras.preprocessing.text import Tokenizer
import pandas as pd
from keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [15]:
# Gantilah 'comments.csv' dengan nama file CSV yang sesuai
df = pd.read_csv('https://huggingface.co/datasets/mabzak/indonesia-youtube-comment/raw/main/comment1.csv')
texts = df['text']

# Membuang baris dengan nilai teks yang hilang
texts = texts.dropna()

# Tokenisasi dan pembuatan representasi numerik dari kata-kata
tokenizer = Tokenizer()
tokenizer.fit_on_texts(texts)
total_words = len(tokenizer.word_index) + 1

In [64]:
tokenizer

In [16]:
input_sequences = []
for line in texts:
    token_list = tokenizer.texts_to_sequences([line])[0]
    for i in range(1, len(token_list)):
        n_gram_sequence = token_list[:i+1]
        input_sequences.append(n_gram_sequence)

max_sequence_length = max([len(x) for x in input_sequences])
input_sequences = pad_sequences(input_sequences, maxlen=max_sequence_length, padding='pre')
predictors, label = input_sequences[:, :-1], input_sequences[:, -1]

In [17]:
import numpy as np

def predict_next_sentence(seed_text, model, tokenizer, max_sequence_length, num_words):
    generated_sentence = seed_text

    for _ in range(num_words):
        token_list = tokenizer.texts_to_sequences([generated_sentence])[0]
        token_list = pad_sequences([token_list], maxlen=max_sequence_length-1, padding='pre')
        predicted_probs = model.predict(token_list, verbose=0)[0]
        predicted_index = np.argmax(predicted_probs)

        # Temukan kata yang sesuai dengan indeks prediksi
        output_word = ""
        for word, index in tokenizer.word_index.items():
            if index == predicted_index:
                output_word = word
                break

        # Tambahkan kata ke kalimat yang dihasilkan
        generated_sentence += " " + output_word

    return generated_sentence


In [21]:
# Menggunakan seed text untuk memprediksi kalimat berikutnya
seed_text = "masa depan negara"
predicted_sentence = predict_next_sentence(seed_text, model, tokenizer, max_sequence_length, num_words=10)
print("Kalimat yang Diprediksi:", predicted_sentence)

Kalimat yang Diprediksi: masa depan negara ini saya yakin bisa di pimpin oleh orang yg baik




---

